In [1]:
import torch
from xgboost import XGBClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

%cd ../Projekt-Magisterski/
from workspace.pose_3d.dataset import KeypointsMatrix
from torch.utils.data import DataLoader
import numpy as np
from matplotlib import pyplot
import pandas as pd

/Users/jakubrzepkowski/Documents/Projekt-magisterski/Repozytorium/Projekt-Magisterski


In [13]:
out_root = '/Users/jakubrzepkowski/Documents/Projekt-magisterski/experiments/made/xgboost_parameters.csv'


In [ ]:
df_empty = pd.DataFrame(columns=['run', 'score', 'runs', 'eta', 'max_depth', 'subsample', 'tree'])
df_empty.to_csv(out_root, index=False)

In [3]:
def dataframe_read(path):
    df = pd.read_csv(out_root).reset_index(drop=True)
    df = df[df['run'] != 'run'].sort_values(by=(['run']),ascending=False)
    return df

In [4]:
def plot(score, results):
    print('Accuracy: %.3f' % score)
    pyplot.plot(results['validation_0']['logloss'], label='train')
    pyplot.plot(results['validation_1']['logloss'], label='test')
    # show the legend
    pyplot.legend()
    # show the plot
    pyplot.show()

In [5]:
def data_loading(training_set, test_set):
    x_train, y_train = [], []
    for idx in range(len(training_set)):
        x, y = training_set[idx]
        x_train.append(x.flatten())
        y_train.append(y.flatten())

    x_train, y_train = np.stack(x_train, axis=0), np.stack(y_train, axis=0)

    x_test, y_test = [], []
    for idx in range(len(test_set)):
        x, y = test_set[idx]
        x_test.append(x.flatten())
        y_test.append(y.flatten())

    x_test, y_test = np.stack(x_test, axis=0), np.stack(y_test, axis=0)
    
    return x_train, y_train, x_test, y_test

In [6]:
# define the model
def model_train(x_train, y_train, x_test, y_test, n_estimators, eta, max_depth, subsample, colsample_bytree):
    
    model = XGBClassifier(n_estimators=n_estimators,
                          eta=eta,
                          max_depth=max_depth,
                          subsample = subsample,
                          colsample_bytree=colsample_bytree,
                          gamma = 1,
                          early_stopping_rounds=10,
                          random_state=1,
                         )

    # define the datasets to evaluate each iteration
    evalset = [(x_train, y_train), (x_test,y_test)]

    model.fit(x_train, y_train, eval_metric='logloss', eval_set=evalset)

    # evaluate performance
    yhat = model.predict(x_test)
    score = accuracy_score(y_test, yhat)
    print('Accuracy: %.3f' % score)
    results = model.evals_result()
    return score, results

In [9]:
def parameters_searching(name, eta, camera=None, cordinates=False, height=False, min_max=False, cg=False, vf=False, select=False):
    training_set = KeypointsMatrix('/Users/jakubrzepkowski/Documents/Projekt-magisterski/dataset/folds/made/train_made_balance.csv',
                                   camera=camera, cordinates_move=cordinates, height_normalize=height, signal_normalize_0_1=min_max,
                                   cg=cg, vf=vf, choose_points=select)
    
    test_set = KeypointsMatrix('/Users/jakubrzepkowski/Documents/Projekt-magisterski/dataset/folds/made/val_made_balance.csv',
                                   camera=camera, cordinates_move=cordinates, height_normalize=height, signal_normalize_0_1=min_max,
                                   cg=cg, vf=vf, choose_points=select)
    
    x_train, y_train, x_test, y_test = data_loading(training_set, test_set)
    
    eta = eta
    n_estimators = 4000
    best_score = 0
    best_result = None
    best_hyperparameters = []
    
    for depth in [7,8,9,10, 11, 12, 14]:
        for subsample in [0.3, 0.5, 0.7, 0.9]:
            for tree in [0.3, 0.5, 0.7, 0.9]:
                score, results = model_train(x_train, y_train, x_test, y_test, n_estimators=n_estimators, eta=eta, max_depth=depth, subsample=subsample, colsample_bytree=tree)
                if score > best_score:
                    best_result = results
                    best_score = score
                    best_hyperparameters.append([name, score*100, n_estimators, eta, depth, subsample, tree])
    
    df_001_side_cords_move_height_001 = pd.DataFrame(best_hyperparameters, columns=['run', 'score', 'runs', 'eta', 'max_depth', 'subsample', 'tree'])
    df_001_side_cords_move_height_001.to_csv(out_root, index=False, mode='a', header=False)

In [11]:
parameters_searching('001_cg_base_side_all_kpts', 0.01, camera='side', cg=True)

[0]	validation_0-logloss:0.69107	validation_1-logloss:0.69244
[1]	validation_0-logloss:0.68906	validation_1-logloss:0.69105
[2]	validation_0-logloss:0.68673	validation_1-logloss:0.68985
[3]	validation_0-logloss:0.68473	validation_1-logloss:0.68891
[4]	validation_0-logloss:0.68263	validation_1-logloss:0.68760
[5]	validation_0-logloss:0.68032	validation_1-logloss:0.68564
[6]	validation_0-logloss:0.67810	validation_1-logloss:0.68422
[7]	validation_0-logloss:0.67609	validation_1-logloss:0.68349


/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[8]	validation_0-logloss:0.67393	validation_1-logloss:0.68234
[9]	validation_0-logloss:0.67183	validation_1-logloss:0.68104
[10]	validation_0-logloss:0.67012	validation_1-logloss:0.67995
[11]	validation_0-logloss:0.66812	validation_1-logloss:0.67926
[12]	validation_0-logloss:0.66637	validation_1-logloss:0.67845
[13]	validation_0-logloss:0.66459	validation_1-logloss:0.67757
[14]	validation_0-logloss:0.66278	validation_1-logloss:0.67612
[15]	validation_0-logloss:0.66096	validation_1-logloss:0.67505
[16]	validation_0-logloss:0.65917	validation_1-logloss:0.67397
[17]	validation_0-logloss:0.65722	validation_1-logloss:0.67350
[18]	validation_0-logloss:0.65534	validation_1-logloss:0.67279
[19]	validation_0-logloss:0.65369	validation_1-logloss:0.67202
[20]	validation_0-logloss:0.65185	validation_1-logloss:0.67111
[21]	validation_0-logloss:0.65000	validation_1-logloss:0.67051
[22]	validation_0-logloss:0.64831	validation_1-logloss:0.66966
[23]	validation_0-logloss:0.64650	validation_1-logloss:0.

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[4]	validation_0-logloss:0.68254	validation_1-logloss:0.68827
[5]	validation_0-logloss:0.68013	validation_1-logloss:0.68658
[6]	validation_0-logloss:0.67786	validation_1-logloss:0.68540
[7]	validation_0-logloss:0.67606	validation_1-logloss:0.68457
[8]	validation_0-logloss:0.67397	validation_1-logloss:0.68350
[9]	validation_0-logloss:0.67177	validation_1-logloss:0.68221
[10]	validation_0-logloss:0.67005	validation_1-logloss:0.68121
[11]	validation_0-logloss:0.66801	validation_1-logloss:0.68007
[12]	validation_0-logloss:0.66621	validation_1-logloss:0.67924
[13]	validation_0-logloss:0.66416	validation_1-logloss:0.67840
[14]	validation_0-logloss:0.66220	validation_1-logloss:0.67791
[15]	validation_0-logloss:0.66019	validation_1-logloss:0.67678
[16]	validation_0-logloss:0.65821	validation_1-logloss:0.67528
[17]	validation_0-logloss:0.65645	validation_1-logloss:0.67444
[18]	validation_0-logloss:0.65463	validation_1-logloss:0.67363
[19]	validation_0-logloss:0.65261	validation_1-logloss:0.6730

...

[1]	validation_0-logloss:0.68211	validation_1-logloss:0.69134
[2]	validation_0-logloss:0.67675	validation_1-logloss:0.69001
[3]	validation_0-logloss:0.67155	validation_1-logloss:0.68887
[4]	validation_0-logloss:0.66650	validation_1-logloss:0.68747
[5]	validation_0-logloss:0.66242	validation_1-logloss:0.68647
[6]	validation_0-logloss:0.65791	validation_1-logloss:0.68533
[7]	validation_0-logloss:0.65308	validation_1-logloss:0.68437
[8]	validation_0-logloss:0.64824	validation_1-logloss:0.68328
[9]	validation_0-logloss:0.64337	validation_1-logloss:0.68229
[10]	validation_0-logloss:0.63885	validation_1-logloss:0.68114
[11]	validation_0-logloss:0.63415	validation_1-logloss:0.67992
[12]	validation_0-logloss:0.62938	validation_1-logloss:0.67879
[13]	validation_0-logloss:0.62460	validation_1-logloss:0.67749
[14]	validation_0-logloss:0.62017	validation_1-logloss:0.67632
[15]	validation_0-logloss:0.61564	validation_1-logloss:0.67517
[16]	validation_0-logloss:0.61104	validation_1-logloss:0.67375
[

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[0]	validation_0-logloss:0.68738	validation_1-logloss:0.69201
[1]	validation_0-logloss:0.68202	validation_1-logloss:0.69062
[2]	validation_0-logloss:0.67684	validation_1-logloss:0.68941
[3]	validation_0-logloss:0.67150	validation_1-logloss:0.68796
[4]	validation_0-logloss:0.66624	validation_1-logloss:0.68683
[5]	validation_0-logloss:0.66152	validation_1-logloss:0.68552
[6]	validation_0-logloss:0.65654	validation_1-logloss:0.68451
[7]	validation_0-logloss:0.65161	validation_1-logloss:0.68332
[8]	validation_0-logloss:0.64666	validation_1-logloss:0.68197
[9]	validation_0-logloss:0.64167	validation_1-logloss:0.68093
[10]	validation_0-logloss:0.63681	validation_1-logloss:0.68050
[11]	validation_0-logloss:0.63190	validation_1-logloss:0.67942
[12]	validation_0-logloss:0.62696	validation_1-logloss:0.67824
[13]	validation_0-logloss:0.62249	validation_1-logloss:0.67699
[14]	validation_0-logloss:0.61797	validation_1-logloss:0.67598
[15]	validation_0-logloss:0.61374	validation_1-logloss:0.67511
[1

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[0]	validation_0-logloss:0.68738	validation_1-logloss:0.69216
[1]	validation_0-logloss:0.68189	validation_1-logloss:0.69084
[2]	validation_0-logloss:0.67647	validation_1-logloss:0.68969
[3]	validation_0-logloss:0.67089	validation_1-logloss:0.68839
[4]	validation_0-logloss:0.66588	validation_1-logloss:0.68709
[5]	validation_0-logloss:0.66081	validation_1-logloss:0.68568
[6]	validation_0-logloss:0.65573	validation_1-logloss:0.68445
[7]	validation_0-logloss:0.65098	validation_1-logloss:0.68321
[8]	validation_0-logloss:0.64598	validation_1-logloss:0.68202
[9]	validation_0-logloss:0.64101	validation_1-logloss:0.68118
[10]	validation_0-logloss:0.63664	validation_1-logloss:0.68012
[11]	validation_0-logloss:0.63169	validation_1-logloss:0.67899
[12]	validation_0-logloss:0.62696	validation_1-logloss:0.67793
[13]	validation_0-logloss:0.62213	validation_1-logloss:0.67700
[14]	validation_0-logloss:0.61745	validation_1-logloss:0.67581
[15]	validation_0-logloss:0.61322	validation_1-logloss:0.67488
[1

In [14]:
parameters_searching('001_cg_base_all_kpts', 0.01, camera=None, cg=True)

[0]	validation_0-logloss:0.69147	validation_1-logloss:0.69208
[1]	validation_0-logloss:0.68975	validation_1-logloss:0.69133
[2]	validation_0-logloss:0.68831	validation_1-logloss:0.69059


/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[3]	validation_0-logloss:0.68665	validation_1-logloss:0.68990
[4]	validation_0-logloss:0.68524	validation_1-logloss:0.68923
[5]	validation_0-logloss:0.68338	validation_1-logloss:0.68795
[6]	validation_0-logloss:0.68174	validation_1-logloss:0.68701
[7]	validation_0-logloss:0.67999	validation_1-logloss:0.68602
[8]	validation_0-logloss:0.67872	validation_1-logloss:0.68532
[9]	validation_0-logloss:0.67725	validation_1-logloss:0.68440
[10]	validation_0-logloss:0.67579	validation_1-logloss:0.68351
[11]	validation_0-logloss:0.67420	validation_1-logloss:0.68270
[12]	validation_0-logloss:0.67264	validation_1-logloss:0.68193
[13]	validation_0-logloss:0.67113	validation_1-logloss:0.68142
[14]	validation_0-logloss:0.66967	validation_1-logloss:0.68077
[15]	validation_0-logloss:0.66803	validation_1-logloss:0.68000
[16]	validation_0-logloss:0.66665	validation_1-logloss:0.67918
[17]	validation_0-logloss:0.66516	validation_1-logloss:0.67856
[18]	validation_0-logloss:0.66371	validation_1-logloss:0.67783

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[2]	validation_0-logloss:0.68796	validation_1-logloss:0.69009
[3]	validation_0-logloss:0.68641	validation_1-logloss:0.68911
[4]	validation_0-logloss:0.68474	validation_1-logloss:0.68841
[5]	validation_0-logloss:0.68290	validation_1-logloss:0.68769
[6]	validation_0-logloss:0.68121	validation_1-logloss:0.68672
[7]	validation_0-logloss:0.67963	validation_1-logloss:0.68592
[8]	validation_0-logloss:0.67838	validation_1-logloss:0.68547
[9]	validation_0-logloss:0.67686	validation_1-logloss:0.68438
[10]	validation_0-logloss:0.67527	validation_1-logloss:0.68367
[11]	validation_0-logloss:0.67350	validation_1-logloss:0.68254
[12]	validation_0-logloss:0.67188	validation_1-logloss:0.68175
[13]	validation_0-logloss:0.67024	validation_1-logloss:0.68121
[14]	validation_0-logloss:0.66873	validation_1-logloss:0.68048
[15]	validation_0-logloss:0.66695	validation_1-logloss:0.67950
[16]	validation_0-logloss:0.66553	validation_1-logloss:0.67887
[17]	validation_0-logloss:0.66407	validation_1-logloss:0.67816


...

[0]	validation_0-logloss:0.68848	validation_1-logloss:0.69162
[1]	validation_0-logloss:0.68383	validation_1-logloss:0.69022
[2]	validation_0-logloss:0.67970	validation_1-logloss:0.68916
[3]	validation_0-logloss:0.67524	validation_1-logloss:0.68811
[4]	validation_0-logloss:0.67114	validation_1-logloss:0.68691
[5]	validation_0-logloss:0.66707	validation_1-logloss:0.68568
[6]	validation_0-logloss:0.66318	validation_1-logloss:0.68469
[7]	validation_0-logloss:0.65920	validation_1-logloss:0.68362
[8]	validation_0-logloss:0.65470	validation_1-logloss:0.68249
[9]	validation_0-logloss:0.65063	validation_1-logloss:0.68148
[10]	validation_0-logloss:0.64684	validation_1-logloss:0.68067
[11]	validation_0-logloss:0.64297	validation_1-logloss:0.67972
[12]	validation_0-logloss:0.63955	validation_1-logloss:0.67904
[13]	validation_0-logloss:0.63616	validation_1-logloss:0.67826
[14]	validation_0-logloss:0.63236	validation_1-logloss:0.67721
[15]	validation_0-logloss:0.62879	validation_1-logloss:0.67641
[1

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[0]	validation_0-logloss:0.68849	validation_1-logloss:0.69170
[1]	validation_0-logloss:0.68352	validation_1-logloss:0.69033
[2]	validation_0-logloss:0.67881	validation_1-logloss:0.68924
[3]	validation_0-logloss:0.67420	validation_1-logloss:0.68805
[4]	validation_0-logloss:0.66983	validation_1-logloss:0.68678
[5]	validation_0-logloss:0.66547	validation_1-logloss:0.68565
[6]	validation_0-logloss:0.66113	validation_1-logloss:0.68439
[7]	validation_0-logloss:0.65719	validation_1-logloss:0.68331
[8]	validation_0-logloss:0.65279	validation_1-logloss:0.68229
[9]	validation_0-logloss:0.64832	validation_1-logloss:0.68132
[10]	validation_0-logloss:0.64435	validation_1-logloss:0.68043
[11]	validation_0-logloss:0.64057	validation_1-logloss:0.67945
[12]	validation_0-logloss:0.63665	validation_1-logloss:0.67848
[13]	validation_0-logloss:0.63312	validation_1-logloss:0.67763
[14]	validation_0-logloss:0.62924	validation_1-logloss:0.67681
[15]	validation_0-logloss:0.62588	validation_1-logloss:0.67567
[1

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[0]	validation_0-logloss:0.68869	validation_1-logloss:0.69172
[1]	validation_0-logloss:0.68395	validation_1-logloss:0.69091
[2]	validation_0-logloss:0.67936	validation_1-logloss:0.69000
[3]	validation_0-logloss:0.67474	validation_1-logloss:0.68898
[4]	validation_0-logloss:0.66954	validation_1-logloss:0.68776
[5]	validation_0-logloss:0.66544	validation_1-logloss:0.68665
[6]	validation_0-logloss:0.66098	validation_1-logloss:0.68543
[7]	validation_0-logloss:0.65656	validation_1-logloss:0.68417
[8]	validation_0-logloss:0.65203	validation_1-logloss:0.68316
[9]	validation_0-logloss:0.64791	validation_1-logloss:0.68227
[10]	validation_0-logloss:0.64401	validation_1-logloss:0.68135
[11]	validation_0-logloss:0.64018	validation_1-logloss:0.68033
[12]	validation_0-logloss:0.63617	validation_1-logloss:0.67928
[13]	validation_0-logloss:0.63266	validation_1-logloss:0.67853
[14]	validation_0-logloss:0.62919	validation_1-logloss:0.67761
[15]	validation_0-logloss:0.62525	validation_1-logloss:0.67688
[1

In [15]:
parameters_searching('001_cg_base_side_selected_kpts', 0.01, camera='side', cg=True, select=True)

[0]	validation_0-logloss:0.69101	validation_1-logloss:0.69230
[1]	validation_0-logloss:0.68885	validation_1-logloss:0.69114
[2]	validation_0-logloss:0.68675	validation_1-logloss:0.68996
[3]	validation_0-logloss:0.68472	validation_1-logloss:0.68864


/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[4]	validation_0-logloss:0.68286	validation_1-logloss:0.68763
[5]	validation_0-logloss:0.68083	validation_1-logloss:0.68657
[6]	validation_0-logloss:0.67878	validation_1-logloss:0.68521
[7]	validation_0-logloss:0.67689	validation_1-logloss:0.68472
[8]	validation_0-logloss:0.67473	validation_1-logloss:0.68406
[9]	validation_0-logloss:0.67290	validation_1-logloss:0.68283
[10]	validation_0-logloss:0.67114	validation_1-logloss:0.68155
[11]	validation_0-logloss:0.66922	validation_1-logloss:0.68071
[12]	validation_0-logloss:0.66739	validation_1-logloss:0.67965
[13]	validation_0-logloss:0.66542	validation_1-logloss:0.67886
[14]	validation_0-logloss:0.66373	validation_1-logloss:0.67817
[15]	validation_0-logloss:0.66212	validation_1-logloss:0.67727
[16]	validation_0-logloss:0.66015	validation_1-logloss:0.67626
[17]	validation_0-logloss:0.65837	validation_1-logloss:0.67523
[18]	validation_0-logloss:0.65673	validation_1-logloss:0.67429
[19]	validation_0-logloss:0.65492	validation_1-logloss:0.6733

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[6]	validation_0-logloss:0.67888	validation_1-logloss:0.68591
[7]	validation_0-logloss:0.67676	validation_1-logloss:0.68538
[8]	validation_0-logloss:0.67459	validation_1-logloss:0.68457
[9]	validation_0-logloss:0.67263	validation_1-logloss:0.68330
[10]	validation_0-logloss:0.67042	validation_1-logloss:0.68239
[11]	validation_0-logloss:0.66864	validation_1-logloss:0.68121
[12]	validation_0-logloss:0.66694	validation_1-logloss:0.68035
[13]	validation_0-logloss:0.66501	validation_1-logloss:0.67986
[14]	validation_0-logloss:0.66305	validation_1-logloss:0.67870
[15]	validation_0-logloss:0.66100	validation_1-logloss:0.67763
[16]	validation_0-logloss:0.65899	validation_1-logloss:0.67645
[17]	validation_0-logloss:0.65716	validation_1-logloss:0.67558
[18]	validation_0-logloss:0.65516	validation_1-logloss:0.67503
[19]	validation_0-logloss:0.65329	validation_1-logloss:0.67413
[20]	validation_0-logloss:0.65132	validation_1-logloss:0.67293
[21]	validation_0-logloss:0.64966	validation_1-logloss:0.67

...

[0]	validation_0-logloss:0.68776	validation_1-logloss:0.69196
[1]	validation_0-logloss:0.68293	validation_1-logloss:0.69075
[2]	validation_0-logloss:0.67794	validation_1-logloss:0.68919
[3]	validation_0-logloss:0.67259	validation_1-logloss:0.68770
[4]	validation_0-logloss:0.66747	validation_1-logloss:0.68641
[5]	validation_0-logloss:0.66244	validation_1-logloss:0.68551
[6]	validation_0-logloss:0.65768	validation_1-logloss:0.68436
[7]	validation_0-logloss:0.65265	validation_1-logloss:0.68301
[8]	validation_0-logloss:0.64783	validation_1-logloss:0.68159
[9]	validation_0-logloss:0.64322	validation_1-logloss:0.68086
[10]	validation_0-logloss:0.63860	validation_1-logloss:0.67981
[11]	validation_0-logloss:0.63411	validation_1-logloss:0.67872
[12]	validation_0-logloss:0.62968	validation_1-logloss:0.67775
[13]	validation_0-logloss:0.62558	validation_1-logloss:0.67665
[14]	validation_0-logloss:0.62121	validation_1-logloss:0.67586
[15]	validation_0-logloss:0.61684	validation_1-logloss:0.67498
[1

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[0]	validation_0-logloss:0.68776	validation_1-logloss:0.69191
[1]	validation_0-logloss:0.68268	validation_1-logloss:0.69081
[2]	validation_0-logloss:0.67748	validation_1-logloss:0.68938
[3]	validation_0-logloss:0.67222	validation_1-logloss:0.68842
[4]	validation_0-logloss:0.66728	validation_1-logloss:0.68719
[5]	validation_0-logloss:0.66192	validation_1-logloss:0.68592
[6]	validation_0-logloss:0.65746	validation_1-logloss:0.68480
[7]	validation_0-logloss:0.65271	validation_1-logloss:0.68357
[8]	validation_0-logloss:0.64787	validation_1-logloss:0.68261
[9]	validation_0-logloss:0.64275	validation_1-logloss:0.68129
[10]	validation_0-logloss:0.63780	validation_1-logloss:0.68016
[11]	validation_0-logloss:0.63294	validation_1-logloss:0.67925
[12]	validation_0-logloss:0.62862	validation_1-logloss:0.67799
[13]	validation_0-logloss:0.62447	validation_1-logloss:0.67697
[14]	validation_0-logloss:0.61989	validation_1-logloss:0.67584
[15]	validation_0-logloss:0.61525	validation_1-logloss:0.67480
[1

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[0]	validation_0-logloss:0.68752	validation_1-logloss:0.69217
[1]	validation_0-logloss:0.68231	validation_1-logloss:0.69076
[2]	validation_0-logloss:0.67689	validation_1-logloss:0.68952
[3]	validation_0-logloss:0.67148	validation_1-logloss:0.68853
[4]	validation_0-logloss:0.66632	validation_1-logloss:0.68741
[5]	validation_0-logloss:0.66095	validation_1-logloss:0.68611
[6]	validation_0-logloss:0.65597	validation_1-logloss:0.68490
[7]	validation_0-logloss:0.65095	validation_1-logloss:0.68385
[8]	validation_0-logloss:0.64589	validation_1-logloss:0.68259
[9]	validation_0-logloss:0.64126	validation_1-logloss:0.68152
[10]	validation_0-logloss:0.63678	validation_1-logloss:0.68045
[11]	validation_0-logloss:0.63193	validation_1-logloss:0.67885
[12]	validation_0-logloss:0.62692	validation_1-logloss:0.67780
[13]	validation_0-logloss:0.62272	validation_1-logloss:0.67709
[14]	validation_0-logloss:0.61815	validation_1-logloss:0.67591
[15]	validation_0-logloss:0.61349	validation_1-logloss:0.67508
[1

In [16]:
parameters_searching('001_cg_base_selected_kpts', 0.01, cg=True, select=True)

[0]	validation_0-logloss:0.69169	validation_1-logloss:0.69242
[1]	validation_0-logloss:0.69005	validation_1-logloss:0.69180


/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[2]	validation_0-logloss:0.68857	validation_1-logloss:0.69115
[3]	validation_0-logloss:0.68700	validation_1-logloss:0.69061
[4]	validation_0-logloss:0.68536	validation_1-logloss:0.69002
[5]	validation_0-logloss:0.68363	validation_1-logloss:0.68899
[6]	validation_0-logloss:0.68205	validation_1-logloss:0.68813
[7]	validation_0-logloss:0.68053	validation_1-logloss:0.68716
[8]	validation_0-logloss:0.67934	validation_1-logloss:0.68672
[9]	validation_0-logloss:0.67775	validation_1-logloss:0.68594
[10]	validation_0-logloss:0.67606	validation_1-logloss:0.68524
[11]	validation_0-logloss:0.67455	validation_1-logloss:0.68448
[12]	validation_0-logloss:0.67300	validation_1-logloss:0.68365
[13]	validation_0-logloss:0.67135	validation_1-logloss:0.68289
[14]	validation_0-logloss:0.67003	validation_1-logloss:0.68217
[15]	validation_0-logloss:0.66839	validation_1-logloss:0.68115
[16]	validation_0-logloss:0.66708	validation_1-logloss:0.68035
[17]	validation_0-logloss:0.66583	validation_1-logloss:0.67985


/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[0]	validation_0-logloss:0.69157	validation_1-logloss:0.69240
[1]	validation_0-logloss:0.68982	validation_1-logloss:0.69170
[2]	validation_0-logloss:0.68833	validation_1-logloss:0.69119
[3]	validation_0-logloss:0.68675	validation_1-logloss:0.68998
[4]	validation_0-logloss:0.68509	validation_1-logloss:0.68910
[5]	validation_0-logloss:0.68326	validation_1-logloss:0.68819
[6]	validation_0-logloss:0.68193	validation_1-logloss:0.68754
[7]	validation_0-logloss:0.68032	validation_1-logloss:0.68677
[8]	validation_0-logloss:0.67889	validation_1-logloss:0.68635
[9]	validation_0-logloss:0.67729	validation_1-logloss:0.68587
[10]	validation_0-logloss:0.67582	validation_1-logloss:0.68516
[11]	validation_0-logloss:0.67440	validation_1-logloss:0.68444
[12]	validation_0-logloss:0.67284	validation_1-logloss:0.68352
[13]	validation_0-logloss:0.67127	validation_1-logloss:0.68271
[14]	validation_0-logloss:0.66981	validation_1-logloss:0.68212
[15]	validation_0-logloss:0.66820	validation_1-logloss:0.68118
[1

...

[0]	validation_0-logloss:0.68861	validation_1-logloss:0.69204
[1]	validation_0-logloss:0.68435	validation_1-logloss:0.69090
[2]	validation_0-logloss:0.67970	validation_1-logloss:0.69045
[3]	validation_0-logloss:0.67587	validation_1-logloss:0.68961
[4]	validation_0-logloss:0.67195	validation_1-logloss:0.68873
[5]	validation_0-logloss:0.66811	validation_1-logloss:0.68794
[6]	validation_0-logloss:0.66471	validation_1-logloss:0.68688
[7]	validation_0-logloss:0.66040	validation_1-logloss:0.68595
[8]	validation_0-logloss:0.65663	validation_1-logloss:0.68518
[9]	validation_0-logloss:0.65288	validation_1-logloss:0.68430
[10]	validation_0-logloss:0.64941	validation_1-logloss:0.68324
[11]	validation_0-logloss:0.64599	validation_1-logloss:0.68256
[12]	validation_0-logloss:0.64194	validation_1-logloss:0.68170
[13]	validation_0-logloss:0.63795	validation_1-logloss:0.68098
[14]	validation_0-logloss:0.63431	validation_1-logloss:0.68045
[15]	validation_0-logloss:0.63033	validation_1-logloss:0.67949
[1

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[0]	validation_0-logloss:0.68859	validation_1-logloss:0.69226
[1]	validation_0-logloss:0.68469	validation_1-logloss:0.69103
[2]	validation_0-logloss:0.68026	validation_1-logloss:0.69016
[3]	validation_0-logloss:0.67601	validation_1-logloss:0.68905
[4]	validation_0-logloss:0.67226	validation_1-logloss:0.68788
[5]	validation_0-logloss:0.66838	validation_1-logloss:0.68702
[6]	validation_0-logloss:0.66429	validation_1-logloss:0.68597
[7]	validation_0-logloss:0.66053	validation_1-logloss:0.68542
[8]	validation_0-logloss:0.65688	validation_1-logloss:0.68451
[9]	validation_0-logloss:0.65307	validation_1-logloss:0.68376
[10]	validation_0-logloss:0.64949	validation_1-logloss:0.68290
[11]	validation_0-logloss:0.64566	validation_1-logloss:0.68204
[12]	validation_0-logloss:0.64169	validation_1-logloss:0.68098
[13]	validation_0-logloss:0.63752	validation_1-logloss:0.68046
[14]	validation_0-logloss:0.63415	validation_1-logloss:0.67973
[15]	validation_0-logloss:0.62973	validation_1-logloss:0.67876
[1

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[0]	validation_0-logloss:0.68862	validation_1-logloss:0.69177
[1]	validation_0-logloss:0.68468	validation_1-logloss:0.69064
[2]	validation_0-logloss:0.68030	validation_1-logloss:0.68976
[3]	validation_0-logloss:0.67608	validation_1-logloss:0.68874
[4]	validation_0-logloss:0.67186	validation_1-logloss:0.68762
[5]	validation_0-logloss:0.66822	validation_1-logloss:0.68634
[6]	validation_0-logloss:0.66360	validation_1-logloss:0.68519
[7]	validation_0-logloss:0.65963	validation_1-logloss:0.68453
[8]	validation_0-logloss:0.65545	validation_1-logloss:0.68336
[9]	validation_0-logloss:0.65157	validation_1-logloss:0.68293
[10]	validation_0-logloss:0.64795	validation_1-logloss:0.68214
[11]	validation_0-logloss:0.64413	validation_1-logloss:0.68147
[12]	validation_0-logloss:0.63998	validation_1-logloss:0.68050
[13]	validation_0-logloss:0.63578	validation_1-logloss:0.67965
[14]	validation_0-logloss:0.63245	validation_1-logloss:0.67884
[15]	validation_0-logloss:0.62818	validation_1-logloss:0.67770
[1

In [ ]:
parameters_searching('001_cg_base_selected_kpts_min_max', 0.01, cg=True, select=True, min_max=True)

[0]	validation_0-logloss:0.69154	validation_1-logloss:0.69254
[1]	validation_0-logloss:0.68992	validation_1-logloss:0.69196
[2]	validation_0-logloss:0.68845	validation_1-logloss:0.69106


/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[3]	validation_0-logloss:0.68684	validation_1-logloss:0.69014
[4]	validation_0-logloss:0.68526	validation_1-logloss:0.68939
[5]	validation_0-logloss:0.68354	validation_1-logloss:0.68862
[6]	validation_0-logloss:0.68207	validation_1-logloss:0.68791
[7]	validation_0-logloss:0.68061	validation_1-logloss:0.68721
[8]	validation_0-logloss:0.67913	validation_1-logloss:0.68677
[9]	validation_0-logloss:0.67751	validation_1-logloss:0.68602
[10]	validation_0-logloss:0.67605	validation_1-logloss:0.68539
[11]	validation_0-logloss:0.67464	validation_1-logloss:0.68465
[12]	validation_0-logloss:0.67307	validation_1-logloss:0.68390
[13]	validation_0-logloss:0.67145	validation_1-logloss:0.68309
[14]	validation_0-logloss:0.66985	validation_1-logloss:0.68237
[15]	validation_0-logloss:0.66845	validation_1-logloss:0.68183
[16]	validation_0-logloss:0.66690	validation_1-logloss:0.68136
[17]	validation_0-logloss:0.66536	validation_1-logloss:0.68060
[18]	validation_0-logloss:0.66388	validation_1-logloss:0.67997

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[3]	validation_0-logloss:0.68645	validation_1-logloss:0.69009
[4]	validation_0-logloss:0.68504	validation_1-logloss:0.68928
[5]	validation_0-logloss:0.68317	validation_1-logloss:0.68806
[6]	validation_0-logloss:0.68159	validation_1-logloss:0.68767
[7]	validation_0-logloss:0.68014	validation_1-logloss:0.68691
[8]	validation_0-logloss:0.67875	validation_1-logloss:0.68648
[9]	validation_0-logloss:0.67704	validation_1-logloss:0.68551
[10]	validation_0-logloss:0.67552	validation_1-logloss:0.68464
[11]	validation_0-logloss:0.67399	validation_1-logloss:0.68393
[12]	validation_0-logloss:0.67259	validation_1-logloss:0.68326
[13]	validation_0-logloss:0.67104	validation_1-logloss:0.68257
[14]	validation_0-logloss:0.66931	validation_1-logloss:0.68203
[15]	validation_0-logloss:0.66793	validation_1-logloss:0.68139
[16]	validation_0-logloss:0.66634	validation_1-logloss:0.68070
[17]	validation_0-logloss:0.66479	validation_1-logloss:0.67974
[18]	validation_0-logloss:0.66334	validation_1-logloss:0.67911

...

[1]	validation_0-logloss:0.68493	validation_1-logloss:0.69153
[2]	validation_0-logloss:0.68100	validation_1-logloss:0.69070
[3]	validation_0-logloss:0.67704	validation_1-logloss:0.68962
[4]	validation_0-logloss:0.67279	validation_1-logloss:0.68874
[5]	validation_0-logloss:0.66885	validation_1-logloss:0.68785
[6]	validation_0-logloss:0.66480	validation_1-logloss:0.68687
[7]	validation_0-logloss:0.66097	validation_1-logloss:0.68588
[8]	validation_0-logloss:0.65735	validation_1-logloss:0.68507
[9]	validation_0-logloss:0.65331	validation_1-logloss:0.68427
[10]	validation_0-logloss:0.64997	validation_1-logloss:0.68338
[11]	validation_0-logloss:0.64664	validation_1-logloss:0.68275
[12]	validation_0-logloss:0.64304	validation_1-logloss:0.68190
[13]	validation_0-logloss:0.63938	validation_1-logloss:0.68107
[14]	validation_0-logloss:0.63652	validation_1-logloss:0.68021
[15]	validation_0-logloss:0.63297	validation_1-logloss:0.67985
[16]	validation_0-logloss:0.62962	validation_1-logloss:0.67894
[

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[0]	validation_0-logloss:0.68934	validation_1-logloss:0.69227
[1]	validation_0-logloss:0.68499	validation_1-logloss:0.69112
[2]	validation_0-logloss:0.68089	validation_1-logloss:0.69040
[3]	validation_0-logloss:0.67659	validation_1-logloss:0.68969
[4]	validation_0-logloss:0.67259	validation_1-logloss:0.68860
[5]	validation_0-logloss:0.66890	validation_1-logloss:0.68766
[6]	validation_0-logloss:0.66497	validation_1-logloss:0.68687
[7]	validation_0-logloss:0.66148	validation_1-logloss:0.68609
[8]	validation_0-logloss:0.65785	validation_1-logloss:0.68555
[9]	validation_0-logloss:0.65380	validation_1-logloss:0.68478
[10]	validation_0-logloss:0.65049	validation_1-logloss:0.68379
[11]	validation_0-logloss:0.64689	validation_1-logloss:0.68286
[12]	validation_0-logloss:0.64336	validation_1-logloss:0.68201
[13]	validation_0-logloss:0.63991	validation_1-logloss:0.68142
[14]	validation_0-logloss:0.63628	validation_1-logloss:0.68051
[15]	validation_0-logloss:0.63269	validation_1-logloss:0.67951
[1

/Users/jakubrzepkowski/Documents/Projekt-magisterski/xgb/lib/python3.10/site-packages/xgboost/sklearn.py:835: UserWarning: `eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.
  warnings.warn(


[0]	validation_0-logloss:0.68891	validation_1-logloss:0.69235
[1]	validation_0-logloss:0.68477	validation_1-logloss:0.69158
[2]	validation_0-logloss:0.68057	validation_1-logloss:0.69106
[3]	validation_0-logloss:0.67642	validation_1-logloss:0.69056
[4]	validation_0-logloss:0.67247	validation_1-logloss:0.68968
[5]	validation_0-logloss:0.66866	validation_1-logloss:0.68883
[6]	validation_0-logloss:0.66477	validation_1-logloss:0.68814
[7]	validation_0-logloss:0.66123	validation_1-logloss:0.68709
[8]	validation_0-logloss:0.65742	validation_1-logloss:0.68640
[9]	validation_0-logloss:0.65336	validation_1-logloss:0.68538
[10]	validation_0-logloss:0.65004	validation_1-logloss:0.68480
[11]	validation_0-logloss:0.64626	validation_1-logloss:0.68404
[12]	validation_0-logloss:0.64271	validation_1-logloss:0.68312
[13]	validation_0-logloss:0.63933	validation_1-logloss:0.68229
[14]	validation_0-logloss:0.63552	validation_1-logloss:0.68126
[15]	validation_0-logloss:0.63212	validation_1-logloss:0.68069
[1

In [ ]:
parameters_searching('001_cg_base_side_selected_kpts_min_max', 0.01, camera='side', cg=True, select=True, min_max=True)

In [ ]:
parameters_searching('001_vf_base_side_all_kpts', 0.01, camera='side', vf=True)

In [ ]:
parameters_searching('001_vf_base_all_kpts', 0.01, camera=None, vf=True)

In [ ]:
parameters_searching('001_vf_base_side_selected_kpts', 0.01, camera='side', vf=True, select=True)

In [ ]:
parameters_searching('001_vf_base_selected_kpts', 0.01, vf=True, select=True)

In [ ]:
parameters_searching('001_vf_base_selected_kpts_min_max', 0.01, vf=True, select=True, min_max=True)

In [ ]:
parameters_searching('001_vf_base_side_selected_kpts_min_max', 0.01, camera='side', vf=True, select=True, min_max=True)

In [ ]:
df

In [ ]:
out_root = '/Users/jakubrzepkowski/Documents/Projekt-magisterski/experiments/clean/xgboost_parameters_003.csv'

In [ ]:
df = dataframe_read(out_root)

In [ ]:
df = df.drop(columns = 'tree')

In [ ]:
new_data = pd.DataFrame(df.values, columns=['run', 'score', 'runs', 'eta', 'max_depth', 'subsample', 'tree'])

In [ ]:
new_data.to_csv(out_root, index = False)

In [ ]:
new_data